# TP : Prevision des ventes d'assurance

**Navigation** : [Index](README.md) | [<< ML-4-Evaluation](ML-4-Evaluation.ipynb)

## Objectifs d'apprentissage

A la fin de ce TP, vous saurez :
1. Construire un modele de regression avec ML.NET (SDCA)
2. Separer les donnees en jeux d'entrainement et de test
3. Evaluer les performances d'un modele de regression
4. Comparer une approche frequentiste (ML.NET) avec une approche bayesienne (Infer.NET)
5. Visualiser les predictions avec ScottPlot

### Prerequis
- .NET SDK 9.0+
- Notebooks ML-1 a ML-4 completes
- Connaissances de base en regression

### Duree estimee : 45-60 minutes

In [1]:
#r "nuget: Microsoft.ML, 5.0.0"
#r "nuget: Microsoft.ML.Probabilistic, 0.4.2504.701"
#r "nuget: Microsoft.ML.Probabilistic.Compiler, 0.4.2504.701"
#r "nuget: ScottPlot, 5.0.55"

using System;
using System.Linq;
using Microsoft.ML;
using Microsoft.ML.Data;
using System.Collections.Generic;
using ScottPlot;

Console.WriteLine("Packages charges avec succes !");

The below script needs to be able to find the current output cell; this is an easy method to get it.

Installed Packages Microsoft.ML, 5.0.0 Microsoft.ML.Probabilistic, 0.4.2504.701 Microsoft.ML.Probabilistic.Compiler, 0.4.2504.701 ScottPlot, 5.0.55

Loading extensions from `C:\Users\jsboi\.nuget\packages\skiasharp\2.88.9\interactive-extensions\dotnet\SkiaSharp.DotNet.Interactive.dll`

Packages charges avec succes !


Les packages necessaires sont :
- **Microsoft.ML** : framework principal de machine learning
- **Microsoft.ML.Probabilistic** : inference bayesienne (Infer.NET)
- **ScottPlot** : visualisations 2D interactives

## Partie 1 : Regression simple avec ML.NET

Dans cette premiere partie, nous construisons un modele de regression lineaire avec l'algorithme SDCA (Stochastic Dual Coordinate Ascent) pour predire le montant des ventes d'assurance.

**Approche** : Entrainement sur l'ensemble complet des donnees (sans separation train/test).

### Donnees

| Variable | Type | Description |
|----------|------|-------------|
| Age | float | Age du client |
| Income | float | Revenu annuel |
| FamilyStatus | float | Situation familiale (0=Celibataire, 1=Marie) |
| EducationLevel | float | Niveau d'education (0=Lycee, 1=Licence, 2=Master) |
| ContractType | float | Type de contrat (0=Sante, 1=Invalidite, 2=Vie) |
| ContractDuration | float | Duree du contrat (annees) |
| PremiumAmount | float | Montant de la prime |
| Region | float | Region (0=Urbain, 1=Rural) |
| **SalesAmount** | float | **Variable cible** : montant des ventes |

In [2]:
// Definir les schemas des donnees d'entree et de sortie
public class SalesData
{
    public float Age { get; set; }
    public float Income { get; set; }
    public float FamilyStatus { get; set; }
    public float EducationLevel { get; set; }
    public float ContractType { get; set; }
    public float ContractDuration { get; set; }
    public float PremiumAmount { get; set; }
    public float Region { get; set; }
    public float SalesAmount { get; set; }
}

public class SalesPrediction
{
    [ColumnName("Score")]
    public float SalesAmount { get; set; }
}

// Creer et preparer les donnees d'entrainement
var mlContext = new MLContext(seed: 42);

// Exemple de donnees d'entrainement
var trainingData = new List<SalesData>
{
    new SalesData { Age = 30, Income = 50000, FamilyStatus = 1, EducationLevel = 1, ContractType = 0, ContractDuration = 5, PremiumAmount = 300, Region = 0, SalesAmount = 10000 },
    new SalesData { Age = 45, Income = 75000, FamilyStatus = 1, EducationLevel = 2, ContractType = 1, ContractDuration = 10, PremiumAmount = 500, Region = 0, SalesAmount = 15000 },
    new SalesData { Age = 50, Income = 100000, FamilyStatus = 0, EducationLevel = 2, ContractType = 2, ContractDuration = 15, PremiumAmount = 700, Region = 1, SalesAmount = 20000 },
    new SalesData { Age = 30, Income = 55000, FamilyStatus = 0, EducationLevel = 1, ContractType = 1, ContractDuration = 5, PremiumAmount = 350, Region = 1, SalesAmount = 12000 },
    new SalesData { Age = 40, Income = 60000, FamilyStatus = 1, EducationLevel = 0, ContractType = 0, ContractDuration = 8, PremiumAmount = 400, Region = 0, SalesAmount = 14000 },
    new SalesData { Age = 35, Income = 65000, FamilyStatus = 0, EducationLevel = 2, ContractType = 2, ContractDuration = 7, PremiumAmount = 450, Region = 1, SalesAmount = 16000 },
    new SalesData { Age = 55, Income = 80000, FamilyStatus = 1, EducationLevel = 1, ContractType = 0, ContractDuration = 10, PremiumAmount = 600, Region = 1, SalesAmount = 18000 },
    new SalesData { Age = 25, Income = 40000, FamilyStatus = 0, EducationLevel = 0, ContractType = 1, ContractDuration = 3, PremiumAmount = 250, Region = 0, SalesAmount = 8000 },
    new SalesData { Age = 65, Income = 90000, FamilyStatus = 1, EducationLevel = 2, ContractType = 2, ContractDuration = 12, PremiumAmount = 750, Region = 0, SalesAmount = 22000 },
    new SalesData { Age = 50, Income = 70000, FamilyStatus = 0, EducationLevel = 1, ContractType = 1, ContractDuration = 15, PremiumAmount = 500, Region = 1, SalesAmount = 13000 },
    new SalesData { Age = 38, Income = 72000, FamilyStatus = 1, EducationLevel = 2, ContractType = 0, ContractDuration = 9, PremiumAmount = 520, Region = 1, SalesAmount = 17000 },
    new SalesData { Age = 44, Income = 68000, FamilyStatus = 1, EducationLevel = 1, ContractType = 2, ContractDuration = 11, PremiumAmount = 570, Region = 0, SalesAmount = 19000 },
    new SalesData { Age = 60, Income = 85000, FamilyStatus = 1, EducationLevel = 2, ContractType = 1, ContractDuration = 13, PremiumAmount = 650, Region = 0, SalesAmount = 21000 },
    new SalesData { Age = 27, Income = 44000, FamilyStatus = 0, EducationLevel = 0, ContractType = 0, ContractDuration = 4, PremiumAmount = 300, Region = 1, SalesAmount = 9000 },
    new SalesData { Age = 31, Income = 47000, FamilyStatus = 0, EducationLevel = 1, ContractType = 1, ContractDuration = 6, PremiumAmount = 320, Region = 0, SalesAmount = 11000 },
};

Console.WriteLine($"Nombre d'echantillons : {trainingData.Count}");

// Charger les donnees d'entrainement
var trainingDataView = mlContext.Data.LoadFromEnumerable(trainingData);

// Definir la pipeline d'apprentissage automatique
var pipeline = mlContext.Transforms.Concatenate("Features",
                                                 "Age",
                                                 "Income",
                                                 "FamilyStatus",
                                                 "EducationLevel",
                                                 "ContractType",
                                                 "ContractDuration",
                                                 "PremiumAmount",
                                                 "Region")
    .Append(mlContext.Regression.Trainers.Sdca(labelColumnName: "SalesAmount", maximumNumberOfIterations: 100));

// Entrainer le modele
Console.WriteLine("\nEntrainement du modele SDCA...");
var model = pipeline.Fit(trainingDataView);
Console.WriteLine("Modele entraine avec succes !");

// Evaluer le modele
var testData = trainingDataView;
var predictions = model.Transform(testData);
var metrics = mlContext.Regression.Evaluate(predictions, labelColumnName: "SalesAmount");

Console.WriteLine("\n=== Metriques d'evaluation ===");
Console.WriteLine($"R-squared : {metrics.RSquared:F4}");
Console.WriteLine($"Mean Absolute Error : {metrics.MeanAbsoluteError:F2}");
Console.WriteLine($"Root Mean Squared Error : {metrics.RootMeanSquaredError:F2}");

// Faire une prediction
var predictionFunc = mlContext.Model.CreatePredictionEngine<SalesData, SalesPrediction>(model);
var newSalesData = new SalesData { Age = 35, Income = 60000, FamilyStatus = 1, EducationLevel = 1, ContractType = 0, ContractDuration = 5, PremiumAmount = 400, Region = 0 };
var prediction = predictionFunc.Predict(newSalesData);

Console.WriteLine($"\nPrediction pour Age=35, Income=60000 : {prediction.SalesAmount:F2}");

// Collecter les donnees pour le graphique
var actualSales = trainingData.Select(x => (double)x.SalesAmount).ToArray();
var predictedSales = mlContext.Data.CreateEnumerable<SalesPrediction>(predictions, reuseRowObject: false).Select(x => (double)x.SalesAmount).ToArray();
var ages = trainingData.Select(x => (double)x.Age).ToArray();

// Graphique : Reel vs Predit
var plt = new ScottPlot.Plot();
plt.Title("Ventes reelles vs predites (Partie 1)");
plt.XLabel("Ventes reelles");
plt.YLabel("Ventes predites");

// Ligne diagonale parfaite
var maxVal = Math.Max(actualSales.Max(), predictedSales.Max()) * 1.1;
plt.Add.Line(0, 0, maxVal, maxVal).Color = ScottPlot.Color.FromHex("#CCCCCC");
plt.Add.Line(0, 0, maxVal, maxVal).LinePattern = ScottPlot.LinePattern.Dashed;

// Points de donnees
plt.Add.Scatter(actualSales, predictedSales);

plt.Axes.SetLimits(0, maxVal, 0, maxVal);
display(plt);

Nombre d'echantillons : 15



Entrainement du modele SDCA...


Modele entraine avec succes !



=== Metriques d'evaluation ===


R-squared : -0,1385


Mean Absolute Error : 4113,32


Root Mean Squared Error : 4610,09



Prediction pour Age=35, Income=60000 : 9788,19


ScottPlot.Plot PlottableList index type value 0 ScottPlot.Plottables.LinePlot ScottPlot.Plottables.LinePlot Start Coordinates { X = 0, Y = 0 } X 0 Y 0 AreReal True Rotated Coordinates { X = 0, Y = 0 } X 0 Y 0 AreReal True Rotated Coordinates { X = 0, Y = 0 } X 0 Y 0 AreReal True Rotated Coordinates { X = 0, Y = 0 } End Coordinates { X = 24200,000000000004, Y = 24200,000000000004 } X 24200.000000000004 Y 24200.000000000004 AreReal True Rotated Coordinates { X = 24200,000000000004, Y = 24200,000000000004 } X 24200.000000000004 Y 24200.000000000004 AreReal True Rotated Coordinates { X = 24200,000000000004, Y = 24200,000000000004 } X 24200,000000000004 Y 24200,000000000004 AreReal True Rotated Coordinates { X = 24200,000000000004, Y = 24200,000000000004 } Line CoordinateLine from (0, 0) to (24200,000000000004, 24200,000000000004) XSpan 24200.000000000004 YSpan 24200.000000000004 Slope 1 SlopeRadians 0.7853981633974483 SlopeDegrees 45 YIntercept 0 Length 34223.97 Start Coordinates { X = 0, Y = 0 } X 0 Y 0 AreReal True Rotated Coordinates { X = 0, Y = 0 } X 0 Y 0 AreReal True Rotated Coordinates { X = 0, Y = 0 } End Coordinates { X = 24200,000000000004, Y = 24200,000000000004 } X 24200.000000000004 Y 24200.000000000004 AreReal True Rotated Coordinates { X = 24200,000000000004, Y = 24200,000000000004 } X 24200,000000000004 Y 24200,000000000004 AreReal True Rotated Coordinates { X = 24200,000000000004, Y = 24200,000000000004 } Center Coordinates { X = 12100,000000000002, Y = 12100,000000000002 } X 12100.000000000002 Y 12100.000000000002 AreReal True Rotated Coordinates { X = 12100,000000000002, Y = 12100,000000000002 } X 12100,000000000002 Y 12100,000000000002 AreReal True Rotated Coordinates { X = 12100,000000000002, Y = 12100,000000000002 } X1 0 X2 24200.000000000004 Y1 0 Y2 24200.000000000004 MarkerStyle ScottPlot.MarkerStyle IsVisible True Shape None Size 0 MarkerColor Color #000000 (R=0, G=0, B=0, A=255) R 0 G 0 B 0 A 255 ARGB 4278190080 PremultipliedARGB 4278190080 Luminance 0 Hue 0 Saturation 0 Red 0 Green 0 Blue 0 Alpha 255 LineStyle ScottPlot.LineStyle Width 1 Hairline False HandDrawn False HandDrawnSegmentLength 7 HandDrawnJitter 1.2 Color Color #000000 (R=0, G=0, B=0, A=255) R 0 G 0 B 0 A 255 ARGB 4278190080 PremultipliedARGB 4278190080 Luminance 0 Hue 0 Saturation 0 Red 0 Green 0 Blue 0 Alpha 255 Pattern ScottPlot.LinePattern Intervals [ ] Phase 0 Name Solid IsVisible True AntiAlias True Rounded False StrokeCap Butt StrokeJoin Miter StrokeMiter 4 CanBeRendered True LineWidth 1 LinePattern ScottPlot.LinePattern Intervals [ ] Phase 0 Name Solid LineColor Color #000000 (R=0, G=0, B=0, A=255) R 0 G 0 B 0 A 255 ARGB 4278190080 PremultipliedARGB 4278190080 Luminance 0 Hue 0 Saturation 0 Red 0 Green 0 Blue 0 Alpha 255 FillStyle ScottPlot.FillStyle Color Color #CCCCCC (R=204, G=204, B=204, A=255) R 204 G 204 B 204 A 255 ARGB 4291611852 PremultipliedARGB 4291611852 Luminance 0,8 Hue 0 Saturation 0 Red 204 Green 204 Blue 204 Alpha 255 HatchColor Color #808080 (R=128, G=128, B=128, A=255) R 128 G 128 B 128 A 255 ARGB 4286611584 PremultipliedARGB 4286611584 Luminance 0,5019608 Hue 0 Saturation 0 Red 128 Green 128 Blue 128 Alpha 255 Hatch <null> HasValue True AntiAlias True IsVisible True CanBeRendered True FillColor Color #CCCCCC (R=204, G=204, B=204, A=255) R 204 G 204 B 204 A 255 ARGB 4291611852 PremultipliedARGB 4291611852 Luminance 0.8 Hue 0 Saturation 0 Red 204 Green 204 Blue 204 Alpha 255 FillHatchColor Color #808080 (R=128, G=128, B=128, A=255) R 128 G 128 B 128 A 255 ARGB 4286611584 PremultipliedARGB 4286611584 Luminance 0.5019608 Hue 0 Saturation 0 Red 128 Green 128 Blue 128 Alpha 255 FillHatch <null> CustomRenderer <null> FillOutline False Outline ScottPlot.LineStyle Width 0 Hairline False HandDrawn False HandDrawnSegmentLength 7 HandDrawnJitter 1.2 Color Color #000000 (R=0, G=0, B=0, A=255) R 0 G 0 B 0 A 255 ARGB 4278190080 PremultipliedARGB 4278190080 Luminance 0 Hue 0 Saturation 0 Red 0 Green 0 Blue 0 Alpha 255 Pattern Sc

### Interpretation des resultats (Partie 1)

Ce premier modele presente une **limitation importante** : il utilise les memes donnees pour l'entrainement ET l'evaluation. Cela conduit a un biais d'evaluation (overfitting non detecte).

| Metrique | Signification |
|----------|---------------|
| R-squared | Proportion de variance expliquee (1.0 = parfait) |
| Mean Absolute Error | Erreur moyenne en valeur absolue |

> **Point critique** : Un R eleve sur les donnees d'entrainement ne garantit pas une bonne generalisation.

**Visualisation** : Le graphique montre les ventes reelles (axe X) vs predites (axe Y). Les points proches de la diagonale indiquent de bonnes predictions.

## Partie 2 : Regression amelioree (Train/Test Split)

Pour obtenir une evaluation plus fiable, nous separons les donnees en :
- **80% entrainement** : pour apprendre les parametres du modele
- **20% test** : pour evaluer la generalisation

**Ameliorations par rapport a la Partie 1** :
1. Separation train/test avec `TrainTestSplit`
2. One-hot encoding des variables categorielles
3. Normalisation Min-Max des features
4. Evaluation separee sur train ET test

In [3]:
var mlContext2 = new MLContext(seed: 42);

// Charger les donnees
var fullDataView = mlContext2.Data.LoadFromEnumerable(trainingData);

// Separer les donnees entre entrainement et test (80% entrainement, 20% test)
var trainTestData = mlContext2.Data.TrainTestSplit(fullDataView, testFraction: 0.2);
var trainDataView = trainTestData.TrainSet;
var testDataView = trainTestData.TestSet;

var trainCount = mlContext2.Data.CreateEnumerable<SalesData>(trainDataView, reuseRowObject: false).Count();
var testCount = mlContext2.Data.CreateEnumerable<SalesData>(testDataView, reuseRowObject: false).Count();

Console.WriteLine($"=== Division des donnees ===");
Console.WriteLine($"Entrainement : {trainCount} echantillons (80%)");
Console.WriteLine($"Test : {testCount} echantillons (20%)");

// Definir la pipeline avec preprocessing
var pipeline2 = mlContext2.Transforms.Categorical.OneHotEncoding(new[]
    {
        new InputOutputColumnPair("FamilyStatus"),
        new InputOutputColumnPair("EducationLevel"),
        new InputOutputColumnPair("ContractType"),
        new InputOutputColumnPair("Region")
    })
    .Append(mlContext2.Transforms.Concatenate("Features",
                                             "Age",
                                             "Income",
                                             "FamilyStatus",
                                             "EducationLevel",
                                             "ContractType",
                                             "ContractDuration",
                                             "PremiumAmount",
                                             "Region"))
    .Append(mlContext2.Transforms.NormalizeMinMax("Features"))
    .Append(mlContext2.Regression.Trainers.Sdca(labelColumnName: "SalesAmount", maximumNumberOfIterations: 100));

// Entrainer le modele
Console.WriteLine("\nEntrainement du modele ameliore...");
var model2 = pipeline2.Fit(trainDataView);
Console.WriteLine("Modele entraine avec succes !");

// Evaluer sur le jeu d'entrainement
var trainPredictions = model2.Transform(trainDataView);
var trainMetrics = mlContext2.Regression.Evaluate(trainPredictions, labelColumnName: "SalesAmount");

// Evaluer sur le jeu de test
var testPredictions = model2.Transform(testDataView);
var testMetrics = mlContext2.Regression.Evaluate(testPredictions, labelColumnName: "SalesAmount");

Console.WriteLine("\n=== Performance sur le jeu d'ENTRAINEMENT ===");
Console.WriteLine($"R-squared : {trainMetrics.RSquared:F4}");
Console.WriteLine($"MAE : {trainMetrics.MeanAbsoluteError:F2}");

Console.WriteLine("\n=== Performance sur le jeu de TEST ===");
Console.WriteLine($"R-squared : {testMetrics.RSquared:F4}");
Console.WriteLine($"MAE : {testMetrics.MeanAbsoluteError:F2}");

// Detection de l'overfitting
var overfittingGap = trainMetrics.RSquared - testMetrics.RSquared;
Console.WriteLine($"\n=== Analyse ===");
Console.WriteLine($"Ecart R2 (Train - Test) : {overfittingGap:F4}");
if (overfittingGap > 0.2)
    Console.WriteLine("ATTENTION : Possible surapprentissage detecte !");
else if (overfittingGap < 0.1)
    Console.WriteLine("Bonne generalisation du modele.");

// Faire une prediction
var predictionFunc2 = mlContext2.Model.CreatePredictionEngine<SalesData, SalesPrediction>(model2);
var prediction2 = predictionFunc2.Predict(newSalesData);
Console.WriteLine($"\nPrediction pour Age=35, Income=60000 : {prediction2.SalesAmount:F2}");

// Collecter les donnees pour le graphique
var trainActual = mlContext2.Data.CreateEnumerable<SalesData>(trainDataView, reuseRowObject: false).Select(x => (double)x.SalesAmount).ToArray();
var trainPred = mlContext2.Data.CreateEnumerable<SalesPrediction>(trainPredictions, reuseRowObject: false).Select(x => (double)x.SalesAmount).ToArray();
var testActual = mlContext2.Data.CreateEnumerable<SalesData>(testDataView, reuseRowObject: false).Select(x => (double)x.SalesAmount).ToArray();
var testPred = mlContext2.Data.CreateEnumerable<SalesPrediction>(testPredictions, reuseRowObject: false).Select(x => (double)x.SalesAmount).ToArray();

// Graphique : Reel vs Predit avec distinction Train/Test
var plt2 = new ScottPlot.Plot();
plt2.Title("Ventes reelles vs predites (Partie 2)");
plt2.XLabel("Ventes reelles");
plt2.YLabel("Ventes predites");

// Ligne diagonale parfaite
var maxVal2 = Math.Max(Math.Max(trainActual.Max(), testActual.Max()), Math.Max(trainPred.Max(), testPred.Max())) * 1.1;
var diagLine = plt2.Add.Line(0, 0, maxVal2, maxVal2);
diagLine.Color = ScottPlot.Color.FromHex("#CCCCCC");
diagLine.LinePattern = ScottPlot.LinePattern.Dashed;

// Points Train (bleu)
var trainScatter = plt2.Add.Scatter(trainActual, trainPred);
trainScatter.Color = ScottPlot.Color.FromHex("#1f77b4");
trainScatter.LegendText = "Train";

// Points Test (rouge)
var testScatter = plt2.Add.Scatter(testActual, testPred);
testScatter.Color = ScottPlot.Color.FromHex("#d62728");
testScatter.LegendText = "Test";

plt2.Legend.IsVisible = true;
plt2.Axes.SetLimits(0, maxVal2, 0, maxVal2);
display(plt2);

=== Division des donnees ===


Entrainement : 13 echantillons (80%)


Test : 2 echantillons (20%)



Entrainement du modele ameliore...


Modele entraine avec succes !


...


=== Analyse ===


Ecart R2 (Train - Test) : 0,7016


ATTENTION : Possible surapprentissage detecte !



Prediction pour Age=35, Income=60000 : 12587,14


ScottPlot.Plot PlottableList index type value 0 ScottPlot.Plottables.LinePlot ScottPlot.Plottables.LinePlot Start Coordinates { X = 0, Y = 0 } X 0 Y 0 AreReal True Rotated Coordinates { X = 0, Y = 0 } X 0 Y 0 AreReal True Rotated Coordinates { X = 0, Y = 0 } X 0 Y 0 AreReal True Rotated Coordinates { X = 0, Y = 0 } End Coordinates { X = 24695,999023437504, Y = 24695,999023437504 } X 24695.999023437504 Y 24695.999023437504 AreReal True Rotated Coordinates { X = 24695,999023437504, Y = 24695,999023437504 } X 24695.999023437504 Y 24695.999023437504 AreReal True Rotated Coordinates { X = 24695,999023437504, Y = 24695,999023437504 } X 24695,999023437504 Y 24695,999023437504 AreReal True Rotated Coordinates { X = 24695,999023437504, Y = 24695,999023437504 } Line CoordinateLine from (0, 0) to (24695,999023437504, 24695,999023437504) XSpan 24695.999023437504 YSpan 24695.999023437504 Slope 1 SlopeRadians 0.7853981633974483 SlopeDegrees 45 YIntercept 0 Length 34925.418 Start Coordinates { X = 0, Y = 0 } X 0 Y 0 AreReal True Rotated Coordinates { X = 0, Y = 0 } X 0 Y 0 AreReal True Rotated Coordinates { X = 0, Y = 0 } End Coordinates { X = 24695,999023437504, Y = 24695,999023437504 } X 24695.999023437504 Y 24695.999023437504 AreReal True Rotated Coordinates { X = 24695,999023437504, Y = 24695,999023437504 } X 24695,999023437504 Y 24695,999023437504 AreReal True Rotated Coordinates { X = 24695,999023437504, Y = 24695,999023437504 } Center Coordinates { X = 12347,999511718752, Y = 12347,999511718752 } X 12347.999511718752 Y 12347.999511718752 AreReal True Rotated Coordinates { X = 12347,999511718752, Y = 12347,999511718752 } X 12347,999511718752 Y 12347,999511718752 AreReal True Rotated Coordinates { X = 12347,999511718752, Y = 12347,999511718752 } X1 0 X2 24695.999023437504 Y1 0 Y2 24695.999023437504 MarkerStyle ScottPlot.MarkerStyle IsVisible True Shape None Size 0 MarkerColor Color #000000 (R=0, G=0, B=0, A=255) R 0 G 0 B 0 A 255 ARGB 4278190080 PremultipliedARGB 4278190080 Luminance 0 Hue 0 Saturation 0 Red 0 Green 0 Blue 0 Alpha 255 LineStyle ScottPlot.LineStyle Width 1 Hairline False HandDrawn False HandDrawnSegmentLength 7 HandDrawnJitter 1.2 Color Color #000000 (R=0, G=0, B=0, A=255) R 0 G 0 B 0 A 255 ARGB 4278190080 PremultipliedARGB 4278190080 Luminance 0 Hue 0 Saturation 0 Red 0 Green 0 Blue 0 Alpha 255 Pattern ScottPlot.LinePattern Intervals [ ] Phase 0 Name Solid IsVisible True AntiAlias True Rounded False StrokeCap Butt StrokeJoin Miter StrokeMiter 4 CanBeRendered True LineWidth 1 LinePattern ScottPlot.LinePattern Intervals [ ] Phase 0 Name Solid LineColor Color #000000 (R=0, G=0, B=0, A=255) R 0 G 0 B 0 A 255 ARGB 4278190080 PremultipliedARGB 4278190080 Luminance 0 Hue 0 Saturation 0 Red 0 Green 0 Blue 0 Alpha 255 FillStyle ScottPlot.FillStyle Color Color #CCCCCC (R=204, G=204, B=204, A=255) R 204 G 204 B 204 A 255 ARGB 4291611852 PremultipliedARGB 4291611852 Luminance 0,8 Hue 0 Saturation 0 Red 204 Green 204 Blue 204 Alpha 255 HatchColor Color #808080 (R=128, G=128, B=128, A=255) R 128 G 128 B 128 A 255 ARGB 4286611584 PremultipliedARGB 4286611584 Luminance 0,5019608 Hue 0 Saturation 0 Red 128 Green 128 Blue 128 Alpha 255 Hatch <null> HasValue True AntiAlias True IsVisible True CanBeRendered True FillColor Color #CCCCCC (R=204, G=204, B=204, A=255) R 204 G 204 B 204 A 255 ARGB 4291611852 PremultipliedARGB 4291611852 Luminance 0.8 Hue 0 Saturation 0 Red 204 Green 204 Blue 204 Alpha 255 FillHatchColor Color #808080 (R=128, G=128, B=128, A=255) R 128 G 128 B 128 A 255 ARGB 4286611584 PremultipliedARGB 4286611584 Luminance 0.5019608 Hue 0 Saturation 0 Red 128 Green 128 Blue 128 Alpha 255 FillHatch <null> CustomRenderer <null> FillOutline False Outline ScottPlot.LineStyle Width 0 Hairline False HandDrawn False HandDrawnSegmentLength 7 HandDrawnJitter 1.2 Color Color #000000 (R=0, G=0, B=0, A=255) R 0 G 0 B 0 A 255 ARGB 4278190080 PremultipliedARGB 4278190080 Luminance 0 Hue 0 Saturation 0 Red 0 Green 0 Blue 0 Alpha 255 Pattern S

### Interpretation des resultats (Partie 2)

La separation train/test permet de detecter le **surapprentissage** :

| Scenario | R2 Train, R2 Test | Interpretation |
|----------|-------------------|----------------|
| Overfitting | > 0.95, < 0.5 | Le modele memorise sans generaliser |
| Bon modele | ~ 0.8, ~ 0.75 | Bonne generalisation |
| Underfitting | < 0.5, < 0.5 | Le modele est trop simple |

> **Note** : Avec seulement 15 echantillons, les resultats sont tres sensibles a la repartition aleatoire des donnees.

**Ameliorations apportees** :
- One-hot encoding des variables categorielles
- Normalisation Min-Max pour mettre toutes les features a la meme echelle
- Evaluation separee sur train ET test pour mesurer la generalisation

## Partie 3 : Systeme de cache Infer.NET

La compilation du modele bayesien Infer.NET peut prendre **5-10 minutes** lors de la premiere execution. Pour eviter d'attendre a chaque execution, nous utilisons un **systeme de cache** intelligent.

> **Note importante** :
> - Ce systeme de cache est **mutualise** avec les notebooks Sudoku via `Infer.NETCacheHelper.cs`
> - Apres la premiere compilation, le modele est sauvegarde en DLL et reutilise instantanement
> - Cette partie est concue pour etre executee **interactivement** dans Jupyter
> - Le cache se trouve dans le dossier `CompiledInferNETModels/`

### Architecture du systeme de cache

```
Infer.NET Cache Architecture
+-- CompiledInferNETModels/          # Dossier de cache
|   +-- BayesianSalesModel.cs        # Code source genere
|   +-- BayesianSalesModel.dll       # Modele compile
+-- Infer.NETCacheHelper.cs          # Helper mutualise
```

**Fonctionnalites du helper** :

| Methode | Description |
|---------|-------------|
| `TryLoadPrecompiledModel()` | Charge un modele precompile depuis le cache |
| `SaveGeneratedSource()` | Sauvegarde le code source genere par Infer.NET |
| `LogCacheInfo()` | Affiche l'etat du cache |
| `ClearCache()` | Nettoie le cache pour forcer une recompilation |

In [4]:
#load "Infer.NETCacheHelper.cs"

using Microsoft.ML.Probabilistic.Models;
using Microsoft.ML.Probabilistic.Models.Attributes;
using Microsoft.ML.Probabilistic.Distributions;
using Range = Microsoft.ML.Probabilistic.Models.Range;

// Charger le helper de cache Infer.NET (compile dans le projet .NET)
InferNETCacheHelper.EnsureCacheDirectoryExists();
InferNETCacheHelper.LogCacheInfo("BayesianSalesModel");

Console.WriteLine("\nCache Infer.NET initialise !");

=== Cache Infer.NET pour BayesianSalesModel ===


Dossier cache : CompiledInferNETModels


Modèle DLL : CompiledInferNETModels\BayesianSalesModel.dll


Code source  : CompiledInferNETModels\BayesianSalesModel.cs



Cache Infer.NET initialise !


### Interpretation des resultats (Partie 3)

Le systeme de cache Infer.NET permet d'eviter la **recompilation** a chaque execution :

| Element | Description |
|---------|-------------|
| Cache hit | Le modele est charge depuis la DLL (execution instantanee) |
| Cache miss | Le modele est compile (5-10 min) puis sauvegarde |
| `TryLoadPrecompiledModel()` | Tente de charger une version compilee |
| `SaveGeneratedSource()` | Sauvegarde le code C# genere par Infer.NET |

**Poids posterieurs et incertitude** :

| Observation | Signification |
|-------------|---------------|
| Poids avec moyenne elevee | Le modele bayesien considere cette feature importante |
| Variance elevee | Le modele est incertain sur l'importance de cette feature |
| Moyenne proche de 0 | La feature a peu d'influence sur les ventes |

> **Comparaison** : Si la MAE bayesienne est comparable a la MAE frequentiste malgre seulement 15 echantillons, cela demontre l'avantage de l'approche bayesienne pour les petits jeux de donnees.

**Point cle** : L'incertitude quantifiee par Infer.NET permet de prendre des decisions plus informees que les predictions ponctuelles de ML.NET.

## Resume et conclusion

Ce TP a couvert trois approches de regression pour la prevision des ventes :

| Approche | Avantages | Limites |
|----------|-----------|---------|
| ML.NET simple (Partie 1) | Rapide, facile a mettre en oeuvre | Pas de separation train/test |
| ML.NET ameliore (Partie 2) | Evaluation fiable, preprocessing | Predictions ponctuelles |
| Infer.NET bayesien (Partie 3) | Incertitude quantifiee, regularisation | Plus complexe a implementer |

**Points cles** :
1. Toujours separer les donnees en train/test pour une evaluation fiable
2. L'approche bayesienne est particulierement adaptee aux petits jeux de donnees
3. La normalisation et l'encodage one-hot ameliorent les performances
4. Les graphiques Reel vs Predit permettent de visualiser la qualite des predictions

**Navigation** : [<< ML-4-Evaluation](ML-4-Evaluation.ipynb) | [Index](README.md)